In [ ]:
%pip install "datasets[Audio]" sprakbanken_normalizer 

In [1]:
from datasets import load_dataset, Audio, Dataset, DatasetDict
from datasets import DownloadManager


import pandas as pd

In [19]:
ds = load_dataset("Sprakbanken/nb_samtale", "orthographic")

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

In [22]:

ds["test"][5]

{'source_file_id': '50f-17',
 'segment_id': '0204880-0211988',
 'segment_order': 32,
 'duration': 7.108,
 'overlap_previous': False,
 'overlap_next': False,
 'speaker_id': 'P30',
 'gender': 0,
 'dialect': 1,
 'orthography': 0,
 'source_type': 1,
 'file_name': 'data/test/bm/50f-17_0204880-0211988.wav',
 'transcription': 'så en en innsjø er så naturlig %foreign over akkurat det som har vokst rundt en innsjø.',
 'audio': {'path': "['/home/ingeridd/.cache/huggingface/datasets/downloads/extracted/524e440de8048401464e63381abb9b9ed759ef7aec6b654efddd1fe5fc36cdb5', '/home/ingeridd/.cache/huggingface/datasets/downloads/extracted/c7bad2c598c84deb101bbdd3a04898377e09414d3d857bb2df6793a95bbe8319']/data/test/bm/50f-17_0204880-0211988.wav",
  'array': array([-0.00311279, -0.00344849,  0.00064087, ...,  0.00131226,
          0.00228882,  0.00268555]),
  'sampling_rate': 16000}}

## Text processing: config transcriptions

Process the text transcriptions and create different transcriptions that can be selected by config options

In [2]:
METADATAFILE = "data/metadata.jsonl"

# Load metadata
df = pd.read_json(METADATAFILE, lines=True)

## Preprocess text 

In [3]:

def map_substrings(texts: pd.Series):
    """Certain symbols are too infrequent to be generalised well, 
    so we map them to more frequent symbols."""
    mapper = {
        "á":"a",
        "ä":"a",
        "ô":"o",
        "à":"a",
        "ê":"e",
        "Á":"A",
        "š":"s",
        "đ":"d",
        "č":"c",
        "ž":"z",
        "€":"£",
        "–":" ",
        r"%ee\b": "%eee",
        "%eeee": "%eee",
        r"%eh\b": "%eee",
        "%eeh": "%eee",
        "%ehh": "%eee",
        "%hhh": "%eee",
        "%err": "%eee",
        "%uhh": "%eee",
        "%aaa": "%eee",
        "%ehe": "%heh",
        "%hehe": "%heh",
        "%erm": "%emm",
        "%eem": "%emm",
        "%enm": "%emm",
        r"%mm\b": "%mmm",
        r"%unin\b" : "%unint",
        r"%qq\b": "%qqq",
        
    }
    for key,value in mapper.items():
        texts.replace(key, value, regex=True, inplace=True)
    return texts

for split in ["validation", "train", "test"]:
    df = pd.read_json(f"data/{split}_metadata.jsonl", lines=True)
    map_substrings(df["transcription"])
    df.to_json(f"data/{split}_metadata_preprocessed.jsonl", lines=True, orient="records", force_ascii=False)

### Preprocessing steps (development stage)

In [2]:
from preprocess_transcriptions import normalize_transcription

In [24]:

for split in ["validation", "train", "test"]:
    df = pd.read_json(f"data/{split}_metadata.jsonl", lines=True)

    for config in ["orthographic", "verbatim"]:
        df[config] = df["transcription"].apply(normalize_transcription, config=config)
    df.to_json(f"data/{split}_metadata_preprocessed.jsonl", lines=True, orient="records", force_ascii=False)

In [36]:
texts = df.transcription.copy()


In [15]:
from preprocess_transcriptions import remove_metatags

# fix metatags
config = "orthographic"
split = "validation"
filename = f"data/{split}_metadata_preprocessed.jsonl"
fixdf = pd.read_json(filename, lines=True)
fixdf[config] = fixdf[config].apply(remove_metatags)
fixdf.to_json(filename, lines=True, orient="records", force_ascii=False)


In [17]:
fixdf.verbatim

0         vi er altså mer spennende enn eee kokte poteter
1       men kan du fortelle oss litt hva var det som r...
2       det var ikkje så veldig mye utval i i butikkan...
3       eee og den som gjekk kanskje i bresjen på den ...
4                         eee heldigvis har det endra seg
                              ...                        
1189    riksseglet ble førte dit det meste av liksom k...
1190    så absolutt altså det å besette kunne besette ...
1191    mmm men ikke eee ikke slik at det er noe hoved...
1192    ja for eller så tenker man seg ofte det at det...
1193    jeg tror vi skal runde av men vi begynte jo me...
Name: verbatim, Length: 1194, dtype: object

In [4]:
symbols = {
    "á":"a",
    "ä":"a",
    "ô":"o",
    "à":"a",
    "ê":"e",
    "Á":"A",
    "š":"s",
    "đ":"d",
    "č":"c",
    "ž":"z",
    "€":"£",
    "–":" ",
}
metatags = {
    "%ee": "%eee",
    "%eeee": "%eee",
    "%eh": "%eee",
    "%eeh": "%eee",
    "%ehh": "%eee",
    "%hhh": "%eee",
    "%err": "%eee",
    "%uhh": "%eee",
    "%aaa": "%eee",
    "%ehe": "%heh",
    "%hehe": "%heh",
    "%erm": "%emm",
    "%eem": "%emm",
    "%enm": "%emm",
    "%mm": "%mmm",
    "%unin" : "%unint",
    "%qq": "%qqq",
    
}

In [6]:
d =   {"%ee": "%eee",
    "%eeee": "%eee",
    "%eh": "%eee",
    "%eeh": "%eee",
    "%ehh": "%eee",
    "%hhh": "%eee",
    "%err": "%eee",
    "%uhh": "%eee",
    "%aaa": "%eee",}


"|".join([k.strip("%") for k in d.keys()])

'ee|eeee|eh|eeh|ehh|hhh|err|uhh|aaa'

In [7]:
for k,v in d.items():
    texts.replace(k, v, regex=True, inplace=True)
#texts.replace(regx, "%eee", regex=True, inplace=True)


In [8]:
texts[texts.str.contains("%err", regex=True)]

Series([], Name: transcription, dtype: object)

In [74]:
from sprakbanken_normalizer.inverse_text_normalizer import inv_normalize
import re


def filter_backslash(text, left=True):
    """Substitute backslash notation with the word to the left or right of it."""
    regx = re.compile(r"\b([\w_-]+)\\([\w_-]+)\b")
    if left:
        return regx.sub(r"\1", text)
    else:
        return regx.sub(r"\2", text)

def remove_repeats(text):
    """Remove repeated words."""
    return re.sub(r"\b(\w+\s+)(\1){1,10}", "\1", text)

def map_substrings(texts: pd.Series):
    """Certain symbols are too infrequent to be generalised well, 
    so we map them to more frequent symbols."""
    mapper = {
        "á":"a",
        "ä":"a",
        "ô":"o",
        "à":"a",
        "ê":"e",
        "Á":"A",
        "š":"s",
        "đ":"d",
        "č":"c",
        "ž":"z",
        "€":"£",
        "–":" ",
        "%ee": "%eee",
        "%eeee": "%eee",
        "%eh": "%eee",
        "%eeh": "%eee",
        "%ehh": "%eee",
        "%hhh": "%eee",
        "%err": "%eee",
        "%uhh": "%eee",
        "%aaa": "%eee",
        "%ehe": "%heh",
        "%hehe": "%heh",
        "%erm": "%emm",
        "%eem": "%emm",
        "%enm": "%emm",
        "%mm": "%mmm",
        "%unin" : "%unint",
        "%qq": "%qqq",
        
    }
    for key,value in mapper.items():
        texts.replace(key, value, regex=True, inplace=True)
    return texts

def bracket_metatags(text): 
    """Enclose unintelligible, foreign, overlapping and unknown words in angle brackets."""
    regx = re.compile(r"%(unint|foreign|unk|overlapping)")
    return regx.sub(r"<\1>", text)

def remove_metatags(text): 
    """Remove metatags for hesitations, laughter, paralinguistic sounds etc."""
    return re.sub(r"%\w{3}\s", "", text)

def remove_percentage_sign(text):
    """Remove percentage sign."""
    return re.sub(r"%", "", text)

def remove_false_starts(text):
    """Remove annotations of false starts and interruptions."""
    return re.sub(r"\s\w+£", "", text)

def remove_pound_sign(text):
    """Remove pound sign."""
    return re.sub(r"£", "", text)

def replace_underscore(text):
    """Replace underscore with a single whitespace."""
    return re.sub(r"_", " ", text)

def remove_punctuation(text):
    """Remove punctuation."""
    return re.sub(r"[,\.\!\'-]", "", text)

def normalize_number_words(text):
    """Normalize number words to integers."""
    inv_norm = inv_normalize(text)
    return inv_norm

    # TODO: convert hyphenated year-words to integers
    # TODO: deal with punctuation at the end 

# TODO: combine hyphenated words with numbers (e.g. CO2, C_O-to\CO2)


In [60]:
df["no_punct"] = df.transcription.str.replace('[^\w\s]','')

In [65]:
df.no_punct.head()

0      hallo og velkommen hit til Nasjonalbiblioteket.
1    det er kulturnatt, og det skjer en bråte ting ...
2    vi har ett arrangement til i kveld klokka tjue...
3    vi snakker matkultur og det eksotiske åttitall...
4    og mer spennende enn kokte poteter tør jeg ogs...
Name: no_punct, dtype: object

In [57]:
texts[texts.str.contains(".")].head()

0       hallo og velkommen hit til Nasjonalbiblioteket
1    det er kulturnatt og det skjer en bråte ting o...
2    vi har ett arrangement til i kveld klokka tjue...
3    vi snakker matkultur og det eksotiske åttitall...
4    og mer spennende enn kokte poteter tør jeg ogs...
Name: transcription, dtype: object

In [79]:


def normalize_transcription(transcription: str, config="annotations"):
    """Normalize transcriptions according to orthographic standards, or verbatim."""
    t = transcription
    if config == "annotations":
        # Nothing do, return as is
        return t
    if config == "orthographic":
        t = remove_metatags(t)
        t = remove_false_starts(t)
        t = re.sub(r"CO-to", "CO2", t)
        t = filter_backslash(t, left=False)
        t = normalize_number_words(t)
    elif config == "verbatim":
        t = bracket_metatags(t)
        t = remove_percentage_sign(t)
        t = remove_pound_sign(t)
        t = re.sub(r"C_O-to", "C O to", t)
        t = filter_backslash(t, left=True)
        t = remove_punctuation(t)
    # For both, at the end:
    t = replace_underscore(t)
    return t




In [67]:

hyphenated = "og han har et prosjekt der hvor han tenker seg at algene kan spise opp C_O-to-en\\CO-to-en og så kan mengden alger bli en del av fôret for krill og og det var vel i hovedsak krill sånn som jeg har forstått det og inn i dette nå skjønner de at en algeforsker holder på med sånne type ting."

In [80]:

normalize_transcription(hyphenated, config="verbatim")

'og han har et prosjekt der hvor han tenker seg at algene kan spise opp C O toen og så kan mengden alger bli en del av fôret for krill og og det var vel i hovedsak krill sånn som jeg har forstått det og inn i dette nå skjønner de at en algeforsker holder på med sånne type ting'

In [173]:
texts = map_substrings(df.transcription.copy())

In [174]:

#df["normalized"] = texts.apply(normalize_transcription, verbatim=False)


#apply(normalize_transcription )


In [181]:
df.normalized.iloc[2]

'vi har ett arrangement til i kveld klokka 21 null null om norsk fankultur og Wenche Myhre og det hele, men aller først har vi noe ganske anna på menyen.'

In [90]:
#df["verbatim"] = df.transcription.apply(normalize_transcription, verbatim=True)

In [37]:
pd.set_option('display.max_colwidth', None)

#df[["transcription", "normalized", "verbatim"]].iloc[1]

In [70]:
df["characters"] = df.transcription.apply(lambda x: list(x))
df = df.explode("characters")

In [73]:
df.characters.value_counts().to_csv("data/characters.csv")

In [42]:
#df["metatags"] = df.transcription.str.extractall(r"(\%\w+)", re.IGNORECASE)
metatags = df.transcription.str.extractall(r"(\%\w+)")

metatags.columns = ["metatags"]

In [ ]:
segments_to_correct =[
    "50f-18_0343045-0343993.wav", # € mappes til £ 
    "50f-6_1310935-1312226.wav", # tankestrek til mellomrom 
    "nb-4_4086270-4092450.wav", # èn til én 
    "nb-4_5245120-5268300.wav", # èn til én
    

]

#TODO: mapping mellom uvanlige symboler 
unusual_symbols = """

á,a
ä,a
ô,o
à,a
ê,e
Á,A
š,s
đ,d
č,c
ž,z
€,£
–,
"""
# normalisert + verbatim skal ikke ha samiske tegn, ü, osv. 
# verbatim skal heller ikke ha de minst vanlige bokstavene med aksent. 

# verbatim: fjerne skilletegn 

In [82]:
df.transcription[df.transcription.str.contains("ò")].iloc[0]

'det stod faktisk folk bak disken og dei importerte jo massevis av spennande %eee råvarer og produkt frå Amerika til oljeamerikanarane, så %eee vi var nok litt foran på ein på eit vis %eee ja så men du nemnde òg peparsteik.'

In [43]:

metatags.metatags.value_counts()

metatags
%eee            7666
%heh             802
%emm             615
%mmm             352
%overlapping     337
%unint           318
%foreign         215
%ttt             108
%qqq              67
%unk               8
Name: count, dtype: int64

In [62]:
#from sprakbanken_normalizer.inverse_text_normalizer import yeargrammar


df["last_punct"] = df.transcription.str.extract(r"\w+(.)$")

#last_punct.replace("nan", "", inplace=True)

nonstandard_punct = df["transcription"][df["last_punct"] != "."].tolist()

idx = 7

punct = "."

sentence = nonstandard_punct[idx]
print("Sentence: " + "\n", sentence)

print(inv_normalize(sentence))

standard_orth = right_backslash(sentence)

print(inv_normalize(standard_orth))

no_punct = standard_orth.strip(punct)

print(inv_normalize(no_punct))

token_separated = no_punct.replace("åttitallet", "åtti - tallet")
print(inv_normalize(token_separated))


#convert_nums(mynumstring_nn, nn=True, reverse=True),
#            convert_ords(mynumstring_nn, nn=True, reverse=True),

Sentence: 
 det skulle vere på ein måte utanlandsk, vere importerte råvarer, utanlandske namn, og så vidare og så vidare. 
det skulle vere på ein måte utanlandsk, vere importerte råvarer, utanlandske namn, osv. og så vidare.
det skulle vere på ein måte utanlandsk, vere importerte råvarer, utanlandske namn, osv. og så vidare.
det skulle vere på ein måte utanlandsk, vere importerte råvarer, utanlandske namn, osv. og så vidare.
det skulle vere på ein måte utanlandsk, vere importerte råvarer, utanlandske namn, osv. og så vidare.


In [19]:

inv_normalize(t.strip(".")) + "."

'vi har ett arrangement til i kveld klokka tjueen null null om norsk fankultur og Wenche Myhre og det hele, men aller først har vi noe ganske anna på menyen.'

In [65]:
teststrings = [
    "dagens dato er tjuende juni tjuetjueto",
    "dette er for eksempel en forkortelse",
    "renta er på to komma fire prosent",
    "dette tallet er tre hundre tusen fire hundre og tjueto",
    "denne setninga skal ikke normaliseres og inneholder æøå-",
    "blant annet satt hun i Statoils sitt styre store deler av nittenåtti-tallet",
    "tjuesekstiåtte",
    "totusenogén",
    "nittenhundreogfire",
    "ni og et halvt tusen",
    "av den årsak er det viktig å behandle denne loven i dag slik at de også etter den første oktober har en lov til å forho forholde oss til i tilknytning til den her saken",
    "os <ee> Kartverkets tinglysning <INAUDIBLE> så tinglyses omkring én komma seks millioner dokumenter i året",
    "vi har ett arrangement til i kveld klokka tjueen null null om norsk fankultur og Wenche Myhre og det hele."
]
for test in teststrings:
    print("BEFORE: " + test)
    print("AFTER: " + inv_normalize(test))
    print()

BEFORE: dagens dato er tjuende juni tjuetjueto
AFTER: dagens dato er 20. juni 2022

BEFORE: dette er for eksempel en forkortelse
AFTER: dette er f.eks. en forkortelse

BEFORE: renta er på to komma fire prosent
AFTER: renta er på 2,4%

BEFORE: dette tallet er tre hundre tusen fire hundre og tjueto
AFTER: dette tallet er 300422

BEFORE: denne setninga skal ikke normaliseres og inneholder æøå-
AFTER: denne setninga skal ikke normaliseres og inneholder æøå-

BEFORE: blant annet satt hun i Statoils sitt styre store deler av nittenåtti-tallet
AFTER: bl.a. satt hun i Statoils sitt styre store deler av nittenåtti-tallet

BEFORE: tjuesekstiåtte
AFTER: 2068

BEFORE: totusenogén
AFTER: 2001

BEFORE: nittenhundreogfire
AFTER: 1904

BEFORE: ni og et halvt tusen
AFTER: 9500

BEFORE: av den årsak er det viktig å behandle denne loven i dag slik at de også etter den første oktober har en lov til å forho forholde oss til i tilknytning til den her saken
AFTER: av den årsak er det viktig å behandle denne 

In [13]:
teststring = "vi har ett arrangement til i kveld klokka tjueen null null om norsk fankultur og Wenche Myhre og det hele."
print("BEFORE: " + teststring)
print("AFTER: " + inv_normalize(teststring))

BEFORE: vi har ett arrangement til i kveld klokka tjueen null null om norsk fankultur og Wenche Myhre og det hele.
AFTER: vi har ett arrangement til i kveld klokka 21 null null om norsk fankultur og Wenche Myhre og det hele.


In [15]:
# TODO: filter bakstrekord (funksjonsord)

from pathlib import Path
from collections import defaultdict


def construct_backslash_lookup(filepath: str = "baktrekede_funksjonsord.txt") -> dict:
    """Construct a lookup table for backslash notation from a text file."""
    backslash_list = Path(filepath).read_text().splitlines()
    backslash_words = defaultdict(list)

    for line in backslash_list:
        if not line: continue
        if line.endswith(":"):
            lang = line.strip(":").lower()
        else: 
            first, last = line.split("\\")
            backslash_words[lang].append({"verbatim": first, "standard": last})
    return backslash_words

def get_backslash_wordset(backslash_words: dict, orth: str, normalize: bool = True) -> set:
    """Get a set of verbatim or standardized words for a given orthographic standard."""
    style = "standard" if normalize else "verbatim"
    return set(item[style] for item in backslash_words[orth])



In [16]:
backslash_words = construct_backslash_lookup()
get_backslash_wordset(backslash_words, "bokmål", normalize=False)

{'demmes',
 'dokk',
 'dokker',
 'dokkers',
 'hen',
 'hva',
 'kass',
 'korleis',
 'korsen',
 'koss',
 'kossen',
 'kva',
 'vart'}

In [ ]:
# generate dataset card from the loader script
#datasets-cli test path/to/<your-dataset-loading-script> --save_info --all_configs

In [ ]:
### COPIED FROM NPSC

def _generate_examples(self, filepaths):
        """Yields examples from NPSC."""
        data_fields = list(self._info().features.keys())
        data_fields.remove("audio")
        lang_code = None
        if self.config.name.endswith("bokmaal"):
            lang_code = "nb-no"
        elif self.config.name.endswith("nynorsk"):
           lang_code = "nn-no"
        for metadata_path, archive_path in filepaths:
            metadata = {}
            with open(metadata_path) as metadata_file:
                for line in metadata_file.read().split("\n"):
                    if line:
                        metadata_object = json.loads(line)
                        if "path" in metadata_object:
                            metadata_key = metadata_object["path"].split("/", 1)[-1]
                            metadata[metadata_key] = metadata_object
            with open(archive_path, "rb") as archive_fs:
                archive_bytes = io.BytesIO(archive_fs.read())
                with tarfile.open(fileobj=archive_bytes, mode="r") as tar:
                    for audio_file in tar.getmembers():
                        if audio_file.isfile():
                            metadata_key = audio_file.name.split(".mp3", 1)[0].split("/", 1)[-1]
                            audio_bytes = tar.extractfile(audio_file).read()
                            audio_dict = {"bytes": audio_bytes, "path": audio_file.name}
                            fields = {key: metadata[metadata_key][key] for key in data_fields}
                            if lang_code:
                                if lang_code == fields.get("sentence_language_code", "").lower():
                                    yield metadata_key, {"audio": audio_dict, **fields}
                            else:
                                yield metadata_key, {"audio": audio_dict, **fields}

## Load dataset splits

In [ ]:
def split_file_path(row):
    path = row["file_name"]
    pathlist = path.split("/")
    dir_path = "/".join(pathlist[:-1])
    splitname = pathlist[1]
    filename = pathlist[-1]
    return path, dir_path, splitname, filename


def load_metadata(filepath):
    metadata = pd.read_json(filepath, lines=True)
    meta = metadata.dropna()  # drop segments from the dataset metadata file that have NaN-values (music and noise don't have values for gender and dialect)
    meta[['audio', 'file_path', 'split', 'file_name']] = meta.apply(split_file_path, axis=1, result_type='expand')
    return meta 

In [2]:
import datasets
import json
from nb_samtale import _DESCRIPTION, _HOMEPAGE, _LICENSE, _CITATION

# Define dataset info
dataset_info = datasets.DatasetInfo(
            # This is the description that will appear on the datasets page.
            description=_DESCRIPTION,
            # This defines the different columns of the dataset and their types
            # If there's a common (input, target) tuple from the features, uncomment supervised_keys line below and
            # specify them. They'll be used if as_supervised=True in builder.as_dataset.
            # supervised_keys=("sentence", "label"),
            # Homepage of the dataset for documentation
            homepage=_HOMEPAGE,
            # License for the dataset if available
            license=_LICENSE,
            # Citation for the dataset
            citation=_CITATION
        )

In [4]:


def create_split_datasets(splitname: str, meta_df: pd.DataFrame):
    """Create a huggingface dataset for a split with the metadata and push it to huggingface datasets hub."""
    split_df = meta_df[meta_df["split"] == splitname]

    # Write the split metadata to a jsonl file
    #split_df.drop("audio", axis=1).to_json(f"data/{splitname}/metadata.jsonl", orient='records', lines=True, force_ascii=False)

    # Create a huggingface dataset from the split metadata
    dataset = Dataset.from_pandas(split_df, split=splitname, info=dataset_info, preserve_index=False).cast_column("audio", Audio(sampling_rate=16000))

    # cast the features to the correct type
    for colname in ["dialect", "orthography", "source_type", "gender"]: 
        dataset = dataset.class_encode_column(colname)
    return dataset


def preprocess_splits(metadata_filepath: str):
    """Preprocess the metadata and create the huggingface datasets for the splits."""
    metadata = load_metadata(metadata_filepath)
    splits = metadata["split"].unique()
    datasplits = {}
    for split in splits:
        dataset = create_split_datasets(split, metadata)
        dataset.to_pandas().drop("audio", axis=1).to_json(f"data/{split}/metadata.jsonl", orient='records', lines=True, force_ascii=False)
        datasplits[split] = dataset
        #   dataset.push_to_hub('Sprakbanken/nb_samtale', split=split)
    return datasplits

In [5]:
metafilepath = 'data/metadata.jsonl'

dataset = preprocess_splits(metafilepath)



Casting to class labels: 100%|██████████| 1194/1194 [00:00<00:00, 66885.69 examples/s]


In [6]:
dataset["dev"][0]

{'source_file_id': 'nb-1',
 'segment_id': '0100800-0104784',
 'segment_order': 9,
 'duration': 3.984,
 'overlap_previous': False,
 'overlap_next': False,
 'speaker_id': 'P48',
 'gender': 0,
 'dialect': 0,
 'orthography': 0,
 'source_type': 0,
 'file_name': 'nb-1_0100800-0104784.wav',
 'transcription': 'vi er altså mer spennende enn %eee kokte poteter.',
 'audio': {'path': 'data/dev/bm/nb-1_0100800-0104784.wav',
  'array': array([-0.00192261,  0.00140381,  0.00299072, ...,  0.00524902,
          0.00448608,  0.00799561]),
  'sampling_rate': 16000},
 'file_path': 'data/dev/bm',
 'split': 'dev'}

---

## create shards 


In [288]:
from typing import Generator 


def ceildiv(a, b):
    return -(a // -b)

def human_readable_size(size: int, round_off: bool = True):
    """Convert a file size in bytes to a human readable format."""
    for unit in ["B", "KB", "MB", "GB", "TB", "PB"]:
        if size < 1024.0:
            break
        size /= 1024.0
    if round_off:
        return f"{round(size)}{unit}"
    return f"{size:.2f}{unit}"

def get_foldersize(dir_path: str):
    """Get the total byte size of a folder."""
    return sum_filesizes(Path(dir_path).iterdir())

def sum_filesizes(filelist: list):
    """Get the total byte size of all files in a file list."""
    total_size = 0
    for filename in filelist:
        total_size += os.path.getsize(filename)
    return total_size

def create_file_batches(file_dir: str, num: int, size: int) -> Generator:
    """Create a list of files to include in a shard."""
    batch_size = 0
    filelist = []
    for f in Path(file_dir).iterdir():
        if f.is_file():
            if batch_size + f.stat().st_size >= size:
                yield filelist
                filelist = []
                batch_size = 0
            batch_size += f.stat().st_size
            filelist.append(f)
    return filelist

In [292]:
#[(i, human_readable_size(f.stat().st_size)) for i, f in enumerate(Path(data_dir).iterdir())][:10]
shards = create_file_batches("data/train/bm", 10, 500*1024*1024)

[human_readable_size(sum_filesizes(sh), round_off=False) for sh in shards]



['499.97MB', '499.97MB', '499.76MB']

In [269]:
import os 
import tarfile

source_dir = "data"
target_dir = "shards"
max_size = 500 * 1024 * 1024  # ~500MB

metadata_file = "metadata.jsonl"
metadf = load_metadata(Path(source_dir) / metadata_file)

splits = ["train", "dev", "test"]
langs = ["bm", "nn"]

split = "train"
lang = "bm"  
# the smallest dataset partition is dev/nn, ~60MB, and the largest is train/bm, ~1.6GB

data_dir = os.path.join(source_dir, split, lang)
total_shards = ceildiv(get_foldersize(data_dir), max_size)

print(f"Total shards: {total_shards}")
print(f"Total size of files in folder: {human_readable_size(get_foldersize(data_dir), round_off=False)}")


#create_shards(dataset[split], audio_dir, shard_dir, shard_size, split, langs, metadata_file)
#!tar -czvf $split_$lang_$shardnum.tar.gz data/$split/$lang/*.wav


Total shards: 4
Total size: 1.57GB


In [238]:
shard_count = 0
shard_name = f"{split}_{lang}-{(shard_count + 1):04d}.tar.gz"
shard_path = os.path.join(target_dir, shard_name)

shard_path
#for idx, filename in enumerate(os.listdir(data_dir)): 
    #print(idx, filename)

'shards/dev_nn-0001.tar.gz'

In [223]:
human_readable_size(os.path.getsize(os.path.join(source_dir, "metadata.jsonl")), round_off=False)

'4.75MB'

## Draft dataset loader script

In [243]:
_DATA_URL = "https://huggingface.co/datasets/Sprakbanken/nb_samtale/resolve/main/data/{batch}"

_METADATA_URL = "https://huggingface.co/datasets/Sprakbanken/nb_samtale/resolve/dev/data/{split}/metadata.jsonl"

_DATA_SPLITS = {
    "train": [
        "train-00000-of-00005-061bdbf053384eef.parquet",
        "train-00001-of-00005-614293dd049991fc.parquet",
        "train-00002-of-00005-d2365f0dd5270964.parquet",
        "train-00003-of-00005-f4a44d9345ca98f6.parquet",
        "train-00004-of-00005-8b07130ce556d0ce.parquet",
        ],
    "dev": ["dev-00000-of-00001-8ddd802c462e8165.parquet"],
    "test": ["test-00000-of-00001-7cad5ef6694eb6a0.parquet"],

}

In [240]:
from huggingface_hub import hf_hub_url, hf_hub_download

#mdata = hf_hub_download(
#    repo_id="Sprakbanken/nb_samtale", filename="data/train/metadata.jsonl", repo_type="dataset", revision="dev")
batchfile = _DATA_SPLITS["dev"][0]
data = hf_hub_download(
    repo_id="Sprakbanken/nb_samtale", 
    filename=f"data/{batchfile}", 
    repo_type="dataset", 
    revision="main"
)

In [102]:

dl_manager = DownloadManager()

In [244]:
    def _split_generator( dl_manager):
        """Returns SplitGenerators."""
        #config_name = self.config.name
            #if config_name.endswith("bokmaal") or config_name.endswith("nynorsk"):
            #  config_name, *_ = config_name.rsplit("_", 1)
        metadata_path = {}
        audio_path = {}
        split_type = {"train": datasets.Split.TRAIN, "test": datasets.Split.TEST, "dev": datasets.Split.VALIDATION}
        for split in split_type:
            metadata_path[split] = dl_manager.download(_METADATA_URL.format(split=split))
            audio_path[split] = dl_manager.download_and_extract([_DATA_URL.format(batch=batch) for batch in _DATA_SPLITS[split]])

        return [
                datasets.SplitGenerator(
                    name=split_type[split],
                    gen_kwargs={
                        "audio_files": dl_manager.iter_archive(audio_path[split]),
                        "metadata_path": dl_manager.download_and_extract(metadata_path[split]),
                        "split": split,
                    },
                ) for split in split_type
            ]

In [242]:
gen = _split_generator(dl_manager)

Extracting data files: 100%|██████████| 1/1 [00:00<00:00, 1512.55it/s]


In [248]:
kwargs = gen[0].gen_kwargs
#    for key, data in kwargs.items():
 #       print(key, data)
metadata_path = kwargs.get("metadata_path")
audio_files = kwargs["audio_files"]
split = kwargs["split"]
config = "annotations"

In [250]:
    def _generate_tables( metadata_path, audio_files, split):
        for file_idx, file in enumerate(audio_files):
            with open(file, "rb") as f:
                parquet_file = pq.ParquetFile(f)
                try:
                    for batch_idx, record_batch in enumerate(
                        parquet_file.iter_batches(batch_size=10_000)
                    ):
                        pa_table = pa.Table.from_batches([record_batch])
                        # Uncomment for debugging (will print the Arrow table size and elements)
                        # logger.warning(f"pa_table: {pa_table} num rows: {pa_table.num_rows}")
                        # logger.warning('\n'.join(str(pa_table.slice(i, 1).to_pydict()) for i in range(pa_table.num_rows)))
                        yield f"{file_idx}_{batch_idx}", pa_table
                except ValueError as e:
                    #logger.error(f"Failed to read file '{file}' with error {type(e)}: {e}")
                    raise

In [251]:
_generator = _generate_tables(metadata_path, audio_files, split)

In [ ]:
#!/usr/bin/python

import datasets

import pyarrow as pa
import pyarrow.parquet as pq

_DATA_FILES = ['data/combined-00009-of-00013-97a88bccf4215954.parquet',
 'data/combined-00004-of-00013-119d653561443d7b.parquet',
 'data/combined-00007-of-00013-ab54cce4ee6331d0.parquet',
 'data/combined-00002-of-00013-149f5d0d22fe8f52.parquet',
 'data/combined-00003-of-00013-426af6f6064e67dd.parquet',
 'data/combined-00010-of-00013-89d7565c5f0d2e4e.parquet',
 'data/combined-00000-of-00013-36d239509fb9e430.parquet',
 'data/combined-00005-of-00013-363bba92a2b7f737.parquet',
 'data/combined-00006-of-00013-4d4d574c9d87176e.parquet',
 'data/combined-00001-of-00013-d5b44e96ad7d2927.parquet',
 'data/combined-00012-of-00013-84cf41ef75dd5b76.parquet',
 'data/combined-00011-of-00013-4c21766cedd5a4a0.parquet',
 'data/combined-00008-of-00013-674f74b6f2288c61.parquet']

class OOMethodTestDataset(datasets.ArrowBasedBuilder):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, **kwargs)

    def _info(self):
        return datasets.DatasetInfo()

    def _split_generators(self, dl_manager):
        files = _DATA_FILES
        downloaded_files = dl_manager.download(files)

        #print(files)
        #print(downloaded_files)

        return [
            datasets.SplitGenerator(
                name="combined",
                gen_kwargs={
                    "files": downloaded_files,
                },
            ),
        ]
    
    def _generate_tables(self, files):
        for file_idx, file in enumerate(files):
            with open(file, "rb") as f:
                parquet_file = pq.ParquetFile(f)
                try:
                    for batch_idx, record_batch in enumerate(
                        parquet_file.iter_batches(batch_size=10_000)
                    ):
                        pa_table = pa.Table.from_batches([record_batch])
                        # Uncomment for debugging (will print the Arrow table size and elements)
                        # logger.warning(f"pa_table: {pa_table} num rows: {pa_table.num_rows}")
                        # logger.warning('\n'.join(str(pa_table.slice(i, 1).to_pydict()) for i in range(pa_table.num_rows)))
                        yield f"{file_idx}_{batch_idx}", pa_table
                except ValueError as e:
                    #logger.error(f"Failed to read file '{file}' with error {type(e)}: {e}")
                    raise

In [230]:
examples = {}
with open(metadata, encoding="utf-8") as f:
    for row in f:
        data = json.loads(row)
        fname = data["file_name"]
        examples[fname] = {
            **data
        }
        #if self.config.name == "annotations":   # Nothing special to do here   
            #transcription = data["transcription"]
        #    yield examples
        if config == "normalized":
            examples["transcription"] = normalize_transcription(data["transcription"])
         #   yield examples
        elif config == "verbatim":
            examples["transcription"] = verbatim_transcription(data["transcription"])
          #  yield examples

In [234]:
import tarfile
import io
import pyarrow as pa
import pyarrow.parquet as pq

id_ = 1
for path in audio_files:
    with open(path, "rb") as f:
        audio = {"path": path, "bytes": f.read()}
        print(id_, {**examples[path], "audio": audio})
    
        id_ += 1
    if id_ > 2:
        break


#####


In [ ]:
# WIP 
for metadata_path, archive_path in filepaths:
    metadata = {}
    with open(metadata_path) as metadata_file:
        for line in metadata_file.read().split("\n"):
            if line:
                metadata_object = json.loads(line)
                if "path" in metadata_object:
                    metadata_key = metadata_object["path"].split("/", 1)[-1]
                    metadata[metadata_key] = metadata_object
    with open(archive_path, "rb") as archive_fs:
        archive_bytes = io.BytesIO(archive_fs.read())
        with tarfile.open(fileobj=archive_bytes, mode="r") as tar:
            for audio_file in tar.getmembers():
                if audio_file.isfile():
                    metadata_key = audio_file.name.split(".mp3", 1)[0].split("/", 1)[-1]
                    audio_bytes = tar.extractfile(audio_file).read()
                    audio_dict = {"bytes": audio_bytes, "path": audio_file.name}
                    fields = {key: metadata[metadata_key][key] for key in data_fields}
                    if lang_code:
                        if lang_code == fields.get("sentence_language_code", "").lower():
                            yield metadata_key, {"audio": audio_dict, **fields}
                    else:
                        yield metadata_key, {"audio": audio_dict, **fields}

In [ ]:
# WORKING FUNCTION
    # method parameters are unpacked from `gen_kwargs` as given in `_split_generators`
    def _generate_examples(self, metadata, filepaths, split):
        # TODO: This method handles input defined in _split_generators to yield (key, example) tuples from the dataset.
        # The `id_` is for legacy reasons (tfds) and is not important in itself, but must be unique for each example.
        examples = {}
        with open(metadata, encoding="utf-8") as f:
            for row in f:
                data = json.loads(row)
                audio_path = data["file_name"].split("/")[-1]  # get the filename from the filepath
                examples[audio_path] = {
                    **data
                }
                if self.config.name == "annotations":   # Nothing special to do here   
                    #transcription = data["transcription"]
                    yield examples
                if self.config.name == "normalized":
                    examples["transcription"] = normalize_transcription(data["transcription"])
                    yield examples
                elif self.config.name == "verbatim":
                    examples["transcription"] = verbatim_transcription(data["transcription"])
                    yield examples

